## Exercise 1

In [1]:
p = 1000003
g = 2 # generator
Fp = GF(p)
Fp

Finite Field of size 1000003

### Exercise 1a

In [2]:
a = Fp(14494)
hA = Fp(g) ^ a
hA

603533

### Exercise 1b

In [3]:
hB = Fp(227654)
shared_secret = hB ^ a
shared_secret

712997

## Exercise 2

In [4]:
# Define the finite field over which this exercise occurs
p = 239
Fp = GF(p)
Fp

Finite Field of size 239

In [5]:
# Define the parameters of the twisted Edwards curve
a = 91
d = 117 # note to self: watch out with plus/minus signs!

In [6]:
# When defining the point P,
# we need to make sure to assign numbers from the finite field!
P = (Fp(65), Fp(121))
P

(65, 121)

In [7]:
# A function which sums two points on an Edwards curve.
# It assumes that the points are defined in terms of finite field elements.
def edwards_add(P1, P2, a=a, d=d):
    x1 = P1[0]
    x2 = P2[0]
    y1 = P1[1]
    y2 = P2[1]
    
    sum_x = (x1*y2 + y1*x2)/(1 + d*x1*x2*y1*y2)
    sum_y = (y1*y2 - a*x1*x2)/(1 - d*x1*x2*y1*y2)
    return (sum_x, sum_y)

In [8]:
# A recursive function which computes multiplication on a twisted Edwards curve.
# It recursively calls the addition function to obtain the solution to multiplication with (c-1)P, then adds P to obtain cP.
def edwards_multiply(P, c, a=a, d=d):
    assert c >= 0
    if c == 0:
        return (Fp(0), Fp(0))
    if c == 1:
        return P
    return edwards_add(edwards_multiply(P, c-1, a, d), P, a, d)

In [9]:
# For verification purposes, we show the result for 2P
P2 = edwards_multiply(P, 2)
P2

(208, 158)

In [10]:
# As a sanity check, we can see that this is equal to P+P
P2 == edwards_add(P, P)

True

In [11]:
# Finally, we compute 3P
P3 = edwards_multiply(P, 3)
P3

(38, 190)

In [12]:
# As a sanity check, we can see that this is equal to (P+P)+P and P+(P+P)
P3 == edwards_add(edwards_add(P,P), P), P3 == edwards_add(P,edwards_add(P,P))

(True, True)

## Exercise 3

Note that, up to different numbers, this is the same exercise as exercise 4 from https://hyperelliptic.org/tanja/teaching/crypto21/second.pdf.

### The example

In [13]:
m = Integer('The ticket code for entry to the event is 0123456789abcdef',36)
m

14862825871049257655028773217160195782109042996144645240655034515163485417943

In [14]:
m.str(36)

'theticketcodeforentrytotheeventis0123456789abcdef'

### Exercise 3a

In [15]:
n = 22025482441888726596151828037580210653496214995318500244177792057815419084860452102794997828952857497081479129671501030354465069182775254612751
e = 5

In [16]:
a = Integer('The ticket code for entry to the event is 0000000000000000', 36)
a = Integer('The ticket code for entry to the event is 000000', 36)
a.str(36)

'theticketcodeforentrytotheeventis000000'

### Exercise 3b

In [17]:
c = 14945124699106513512945998228173407848267373079612362508758547830348203919947635528123687362242672491106612647574302851824269806227326368236121

In [18]:
X = Integer('zzzzzzzzzzzzzzzz', 36)
X = Integer('zzzzzz', 36)

### New attempt, using matrix computed in Mathematica

In [19]:
M = matrix([
    [X^7, 5*a*X^6, 10*a^2*X^5, 10*a^3*X^4, 5*a^4*X^3, a^5*X^2-c*X^2, 0, 0],
    [0, X^6, 5*a*X^5, 10*a^2*X^4, 10*a^3*X^3, 5*a^4*X^2, a^5*X-c*X, 0],
    [0, 0, X^5, 5*a*X^4, 10*a^2*X^3, 10*a^3*X^2, 5*a^4*X, a^5-c],
    [0, 0, 0, n*X^4, 0, 0, 0, 0],
    [0, 0, 0, 0, n*X^3, 0, 0, 0],
    [0, 0, 0, 0, 0, n*X^2, 0, 0],
    [0, 0, 0, 0, 0, 0, n*X, 0],
    [0, 0, 0, 0, 0, 0, 0, n]
])
B = M.LLL()

In [20]:
Q = B[0][0]*x^7/X^7 + B[0][1]*x^6/X^6 + B[0][2]*x^5/X^5 + B[0][3]*x^4/X^4 + B[0][4]*x^3/X^3 + B[0][5]*x^2/X^2 + B[0][6]*x/X + B[0][7]
Q.roots(ring=ZZ)

[(91137355, 1)]

In [21]:
Q.roots(ring=ZZ)[0][0].str(base=36)

'1i9e17'

<div class="alert alert-success">
    So, we find that the ticket code is <code>1i9e17</code>.
</div>

Still, it might be educative to see whether this attack would have worked with fewer matrix rows and columns. First, let's remove the row (and column) for $x^2\cdot f(x)^2$.

In [22]:
M = matrix([
    [X^6, 5*a*X^5, 10*a^2*X^4, 10*a^3*X^3, 5*a^4*X^2, a^5*X-c*X, 0],
    [0, X^5, 5*a*X^4, 10*a^2*X^3, 10*a^3*X^2, 5*a^4*X, a^5-c],
    [0, 0, n*X^4, 0, 0, 0, 0],
    [0, 0, 0, n*X^3, 0, 0, 0],
    [0, 0, 0, 0, n*X^2, 0, 0],
    [0, 0, 0, 0, 0, n*X, 0],
    [0, 0, 0, 0, 0, 0, n]
])
B = M.LLL()

Q = B[0][0]*x^6/X^6 + B[0][1]*x^5/X^5 + B[0][2]*x^4/X^4 + B[0][3]*x^3/X^3 + B[0][4]*x^2/X^2 + B[0][5]*x/X + B[0][6]
Q.roots(ring=ZZ)
Q.roots(ring=ZZ)[0][0].str(base=36)

'1i9e17'

Now, let's see whether it would still have worked with even fewer matrix rows and columns. This time, we remove the row (and column) for $x\cdot f(x)$.

In [23]:
M = matrix([
    [X^5, 5*a*X^4, 10*a^2*X^3, 10*a^3*X^2, 5*a^4*X, a^5-c],
    [0, n*X^4, 0, 0, 0, 0],
    [0, 0, n*X^3, 0, 0, 0],
    [0, 0, 0, n*X^2, 0, 0],
    [0, 0, 0, 0, n*X, 0],
    [0, 0, 0, 0, 0, n]
])
B = M.LLL()

Q = B[0][0]*x^5/X^5 + B[0][1]*x^4/X^4 + B[0][2]*x^3/X^3 + B[0][3]*x^2/X^2 + B[0][4]*x/X + B[0][5]
Q.roots(ring=ZZ)
Q.roots(ring=ZZ)[0][0].str(base=36)

'1i9e17'

<div class="alert alert-success">
    We see that this would still work. We must have made some mistake in the matrices earlier on...
</div>

<div class="alert alert-warning">
    It seems to be the case that the earlier attempt does work now. Perhaps I wasn't paying attention, or I did not <em>"restart the kernel and run all"</em> sufficiently often... 🤦‍♂️
</div>

In [26]:
# Some verification steps to see why this works.
delta = 3/4
assert M.nrows() == M.ncols() # checks whether matrix is square
len_v_bound = (2/sqrt(4*delta-1))^((M.nrows()-1)/2) * (det(M))^(1/M.nrows())

# We need to have ||g(xX)|| <= b^k/sqrt(d), with b^k = n and d=M.nrows()
# Also, g(xX) = ||v_1||, which was bounded by the LLL-algorithm (see above for the value)
rhs = n^2/sqrt(M.nrows())
lhs = len_v_bound
lhs <= rhs
int(lhs) <= int(rhs)

True